<h2><center>ACCOUNT PREDICTION </center></h2>
<h4><center>Code Document</center></h4>
<h4><center>August 2017</center></h4>

In [28]:
#### Load packages 
%matplotlib inline
import matplotlib.pyplot as plt
import plotly
plotly.offline.init_notebook_mode(connected=True)
from plotly.offline import iplot,plot
from plotly.graph_objs import *
import plotly.tools as tls

In [2]:
import numpy as np
import pandas as pd
import copy

In [3]:
from sklearn.ensemble import RandomForestClassifier 
from sklearn import cluster

In [4]:
from sklearn.cross_validation import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.externals import joblib
from sklearn.utils import resample,shuffle
from sklearn.cross_validation import cross_val_score
import itertools

In [5]:
import collections

#### 1.  Load Data 

In [6]:
cd Desktop 

C:\Users\A458497\Desktop


In [7]:
### Trained Data: Paid invoices of Expense Bis
xl=pd.ExcelFile("facture_comptabilisées_BEX_062016_042017_v2.xlsx")
df=xl.parse('Sheet 1')

df['c1']=pd.DataFrame([str(i)[:1] for i in df.ACCOUNT])
df['c3']=pd.DataFrame([str(i)[:3] for i in df.ACCOUNT])

Clean the lines when the ACCOUNT value is null

In [37]:
df=df[~df.ACCOUNT.isnull()]

In [39]:
df.tail()

BUSINESS_UNIT VENDOR_SETID  VENDOR_ID  MONETARY_AMOUNT  VAT_INV_AMT_GL  \
147002         GIMS1        FR001         19         14976.31            0.00   
147003         DF001        FR001        175         55756.93        10010.22   
147004         DF001        FR001        175            69.88            8.04   
147005         DF001        FR001        175         19126.71            0.00   
147236         IT001        FR001        940           842.18          151.20   

       CURRENCY_CD ASSET_FLG VOUCHER_ID  VOUCHER_LINE_NUM  DISTRIB_LINE_NUM  \
147002         EUR         N   00001915                 1                 1   
147003         EUR         N   AJ265678                 1                 1   
147004         EUR         N   AJ265678                 2                 1   
147005         EUR         N   AJ265678                 3                 1   
147236         EUR         N   IT124757                 1                 1   

       ...  VAT_TREATMENT VAT_SERVICE_TYPE     ACCOUNT ALTACCT TAX_CD_VAT  \
147002 ...            SGI              2.0  99655978.0     NaN      FRNOR   
147003 ...            DGP              2.0  99644592.0     NaN      FRNOR   
147004 ...            DGP              2.0  99644568.0     NaN      FR130   
147005 ...            DGP              2.0  99644568.0     NaN      FR000   
147236 ...            DSP              2.0  99632415.0     NaN      FRNOR   

                          DESCR VNDR_FIELD_C30_J ACTIVE_FLG  c1   c3  
147002                      NaN     2.100000e+09          N   9  996  
147003                      NaN     2.100000e+09          N   9  996  
147004                      NaN     2.100000e+09          N   9  996  
147005                      NaN     2.100000e+09          N   9  996  
147236  EVENEMENTS INTERNES-HTR     2.100001e+09          N   9  996  

[5 rows x 27 columns]

In [40]:
df.describe()

c:\homeware\anaconda3\lib\site-packages\numpy\lib\function_base.py:3834: RuntimeWarning:

Invalid value encountered in percentile



VENDOR_ID  MONETARY_AMOUNT  VAT_INV_AMT_GL  VOUCHER_LINE_NUM  \
count  1.436290e+05     1.436290e+05    1.436290e+05     143629.000000   
mean   6.642918e+08     1.087886e+04    1.227390e+03          1.240752   
std    4.722156e+08     1.614413e+05    1.940047e+04          0.663754   
min    1.000000e+00    -9.240143e+06   -1.658913e+06          1.000000   
25%    7.682000e+03     8.739000e+01    0.000000e+00          1.000000   
50%    1.000001e+09     7.326900e+02    6.040000e+01          1.000000   
75%    1.000006e+09     3.588190e+03    4.345800e+02          1.000000   
max    1.000022e+09     1.613872e+07    1.489491e+06         51.000000   

       DISTRIB_LINE_NUM  VAT_SERVICE_TYPE       ACCOUNT  ALTACCT  \
count     143629.000000          143320.0  1.436290e+05      0.0   
mean           1.063706               2.0  9.754594e+07      NaN   
std            0.722145               0.0  1.143875e+07      NaN   
min            1.000000               2.0  1.052000e+05      NaN   
25%            1.000000               NaN  9.963242e+07      NaN   
50%            1.000000               NaN  9.964613e+07      NaN   
75%            1.000000               NaN  9.965288e+07      NaN   
max           37.000000               2.0  9.976709e+07      NaN   

       VNDR_FIELD_C30_J  
count      1.436170e+05  
mean       2.141496e+09  
std        5.687778e+07  
min        2.227701e+08  
25%                 NaN  
50%                 NaN  
75%                 NaN  
max        2.200022e+09

In [8]:
xl_bu=pd.ExcelFile("BU_hier.xlsx")
bu_hier=xl_bu.parse('Sheet1')
bu_hier["fil"]=pd.DataFrame([str(i)[:3] for i in bu_hier.Column6])

In [42]:
bu_hier.head()

Column6        SSC  Région  Pole BUSINESS_UNIT                   DESCR BU  \
0  Fil/Suc  Paris/Buc  France    DC         S9569            SOGE PERIVAL IV   
1  Fil/Suc  Paris/Buc  France    DC         S6862          SI 29 BD Hausmann   
2  Fil/Suc   Bucarest  France  RBDF         S0010                        CGA   
3  Fil/Suc  Paris/Buc  France    DC         S8990                       STIP   
4  Fil/Suc  Paris/Buc  France    DC         S2273  LA FONCIERE DE LA DEFENSE   

   fil  
0  Fil  
1  Fil  
2  Fil  
3  Fil  
4  Fil

In [1]:
# iplot([{"x":[1,2,3],"y":[3,1,6]}])

#### 1.1 Data analysis

In [10]:
collections.Counter(df.c1)

Counter({'1': 259,
         '2': 6,
         '3': 15,
         '4': 496,
         '6': 4944,
         '7': 16,
         '9': 137893,
         'n': 3743})

In [11]:
collections.Counter(df.c3[df.c1=='9'])

Counter({'990': 79,
         '991': 30,
         '992': 3,
         '993': 16977,
         '994': 22,
         '996': 120602,
         '997': 180})

In [12]:
df.ACCOUNT.unique().shape[0]

445

In [16]:
iplot([Histogram(x=df.c3)])

In [ ]:
iplot([Histogram(x=df.groupby(["VENDOR_ID"]).ACCOUNT.count().reset_index().ACCOUNT)])

In [25]:
df.tail()

BUSINESS_UNIT VENDOR_SETID  VENDOR_ID  MONETARY_AMOUNT  VAT_INV_AMT_GL  \
147367         IT001        FR001      14369          4006.81             0.0   
147368         IT001        FR001      14369          1015.18             0.0   
147369         IT001        FR001      14369          3030.09             0.0   
147370         IT001        FR001      14369          1366.54             0.0   
147371         IT001        FR001       7776         17688.88             0.0   

       CURRENCY_CD ASSET_FLG VOUCHER_ID  VOUCHER_LINE_NUM  DISTRIB_LINE_NUM  \
147367         EUR         N   00003897                 1                 1   
147368         EUR         N   00003898                 1                 1   
147369         EUR         N   00003899                 1                 1   
147370         EUR         N   00003900                 1                 1   
147371         EUR         N   00003901                 1                 1   

       ...  VAT_TREATMENT VAT_SERVICE_TYPE ACCOUNT ALTACCT TAX_CD_VAT  \
147367 ...            DSP              2.0     NaN     NaN      FRNOR   
147368 ...            DSP              2.0     NaN     NaN      FRNOR   
147369 ...            DSP              2.0     NaN     NaN      FRNOR   
147370 ...            DSP              2.0     NaN     NaN      FRNOR   
147371 ...            OOS              2.0     NaN     NaN        NaN   

            DESCR VNDR_FIELD_C30_J ACTIVE_FLG  c1   c3  
147367  generic 1     2.100014e+09          N   n  nan  
147368  generic 1     2.100014e+09          N   n  nan  
147369  generic 1     2.100014e+09          N   n  nan  
147370  generic 1     2.100014e+09          N   n  nan  
147371  generic 1     2.100008e+09          N   n  nan  

[5 rows x 27 columns]

#### 2. New Feature

<ul><li>Probability of each case per Vendor in the historic</li> </ul>

In [44]:
df["count"]=1

1. Active FLG: flag od "LISSAGE"

In [45]:
ga=df[["VENDOR_ID","ACTIVE_FLG","count"]].groupby(["VENDOR_ID","ACTIVE_FLG"])["count"].sum().groupby(level = 0).transform(lambda x: x/x.sum())
gga=df[["VENDOR_ID"]].drop_duplicates()
for name,group in ga.groupby(level=1):
    gi=pd.DataFrame(group.reset_index())[["VENDOR_ID","count"]]
    gi = gi.rename(columns={'count': "AC_"+str(name)})
    gga=gga.merge(gi,on='VENDOR_ID',how='left')
gga=gga.fillna(0.0)

In [47]:
gga.head()

VENDOR_ID      AC_N      AC_Y
0        2286  1.000000  0.000000
1  1000000001  1.000000  0.000000
2         197  0.906977  0.093023
3  1000000666  1.000000  0.000000
4  1000008463  1.000000  0.000000

<ul>
<li>Probability of each case of first number of ACCOUNT for each Vendor in the historic</li> </ul>

In [49]:
g=df[["VENDOR_ID","c1","count"]].groupby(["VENDOR_ID","c1"])["count"].sum().groupby(level = 0).transform(lambda x: x/x.sum())
gg=df[["VENDOR_ID"]].drop_duplicates()
for name,group in g.groupby(level=1):
    gi=pd.DataFrame(group.reset_index())[["VENDOR_ID","count"]]
    gi = gi.rename(columns={'count': "c1_"+str(name)})
    gg=gg.merge(gi,on='VENDOR_ID',how='left')
gg=gg.fillna(0.0)

In [50]:
gg.head()

VENDOR_ID  c1_1  c1_2  c1_3  c1_4  c1_6  c1_7  c1_9
0        2286   0.0   0.0   0.0   0.0   0.0   0.0   1.0
1  1000000001   0.0   0.0   0.0   0.0   0.0   0.0   1.0
2         197   0.0   0.0   0.0   0.0   0.0   0.0   1.0
3  1000000666   0.0   0.0   0.0   0.0   0.0   0.0   1.0
4  1000008463   0.0   0.0   0.0   0.0   0.0   0.0   1.0

for example: the probability for the Vendor_Id= 2286 in the hisotic data, the Prob(first_number _f_account=9)=1 "

• Probability of each possible first 3 number of ACCOUNT for each Vendor in the historic

In [51]:
g3=df[["VENDOR_ID","c3","count"]][df.c1=='9'].groupby(["VENDOR_ID","c3"])["count"].sum().groupby(level = 0).transform(lambda x: x/x.sum())
gg3=df[["VENDOR_ID"]][df.c1=='9'].drop_duplicates()
for name,group in g3.groupby(level=1):
#   print(name)
    gi=pd.DataFrame(group.reset_index())[["VENDOR_ID","count"]]
    gi = gi.rename(columns={'count': "c3_"+str(name)})
    gg3=gg3.merge(gi,on='VENDOR_ID',how='left')
gg3=gg3.fillna(0.0)

In [52]:
g3_c=df[['VNDR_FIELD_C30_J',"c3","count"]][df.c1=='9'].groupby(['VNDR_FIELD_C30_J',"c3"])["count"].sum().groupby(level = 0).transform(lambda x: x/x.sum())
gg3_c=df[['VNDR_FIELD_C30_J']].drop_duplicates()
for name,group in g3_c.groupby(level=1):
#   print(name)
    gi=pd.DataFrame(group.reset_index())[['VNDR_FIELD_C30_J',"count"]]
    gi = gi.rename(columns={'count': "c3_"+str(name)})
    gg3_c=gg3_c.merge(gi,on='VNDR_FIELD_C30_J',how='left')
gg3_c=gg3_c.fillna(0.0)

In [56]:
gg3_c.head()

VNDR_FIELD_C30_J  c3_990  c3_991  c3_992    c3_993  c3_994    c3_996  \
0      2.100002e+09     0.0     0.0     0.0  0.000000     0.0  1.000000   
1      2.100000e+09     0.0     0.0     0.0  0.062500     0.0  0.937500   
2      2.100000e+09     0.0     0.0     0.0  0.071429     0.0  0.928571   
3      2.100003e+09     0.0     0.0     0.0  0.000000     0.0  1.000000   
4      2.200008e+09     0.0     0.0     0.0  0.000000     0.0  1.000000   

   c3_997  
0     0.0  
1     0.0  
2     0.0  
3     0.0  
4     0.0

• Probability of each possible ACCOUNT for each Vendor when the account is begin with 994 or 997 or 993 etc in the historic

In [53]:
g_994=df[["VENDOR_ID","ACCOUNT","count"]][df.c3=='994'].groupby(["VENDOR_ID","ACCOUNT"])["count"].sum().groupby(level = 0).transform(lambda x: x/x.sum())
gg_994=df[["VENDOR_ID"]][df.c3=='994'].drop_duplicates()
for name,group in g_994.groupby(level=1):
    gi=pd.DataFrame(group.reset_index())[["VENDOR_ID","count"]]
    gi = gi.rename(columns={'count': "c994_"+str(name)})
    gg_994=gg_994.merge(gi,on='VENDOR_ID',how='left')
    gg_994=gg_994.fillna(0.0)
gg_994=gg_994.drop_duplicates()

In [54]:
g_997=df[["VENDOR_ID","ACCOUNT","count"]][df.c3=='997'].groupby(["VENDOR_ID","ACCOUNT"])["count"].sum().groupby(level = 0).transform(lambda x: x/x.sum())
gg_997=df[["VENDOR_ID"]][df.c3=='997'].drop_duplicates()
for name,group in g_997.groupby(level=1):
    gi=pd.DataFrame(group.reset_index())[["VENDOR_ID","count"]]
    gi = gi.rename(columns={'count': "c997_"+str(name)})
    gg_997=gg_997.merge(gi,on='VENDOR_ID',how='left')
    gg_997=gg_997.fillna(0.0)
gg_997=gg_997.drop_duplicates()

In [55]:
g_993=df[["VENDOR_ID","ACCOUNT","count"]][df.c3=='993'].groupby(["VENDOR_ID","ACCOUNT"])["count"].sum().groupby(level = 0).transform(lambda x: x/x.sum())
gg_993=df[["VENDOR_ID"]][df.c3=='993'].drop_duplicates()
for name,group in g_993.groupby(level=1):
    gi=pd.DataFrame(group.reset_index())[["VENDOR_ID","count"]]
    gi = gi.rename(columns={'count': "c993_"+str(name)})
    gg_993=gg_993.merge(gi,on='VENDOR_ID',how='left')
    gg_993=gg_993.fillna(0.0)


#### 3.  VENDOR_ID only one Account

<ul><li>Vendor with only on ACCOUNT</li></ul>

In [ ]:
v=df[["VENDOR_ID","ACCOUNT"]]
v_1=v.groupby('VENDOR_ID').ACCOUNT.nunique().reset_index()
v_11=v_1[v_1.ACCOUNT==1]
v_11=v_11[["VENDOR_ID"]].merge(df[["VENDOR_ID","ACCOUNT"]].drop_duplicates(),on="VENDOR_ID",how='left')

<ul><li>Vendor with only on ACCOUNT when the first 3 number is 996 /993/994/993 </li></ul>

In [ ]:
v=df[["VENDOR_ID","ACCOUNT"]][df.c3=='996']
v_1=v.groupby('VENDOR_ID').ACCOUNT.nunique().reset_index()
v_1_996=v_1[v_1.ACCOUNT==1]
v_1_996=v_1_996[["VENDOR_ID"]].merge(df[["VENDOR_ID","ACCOUNT"]][df.c3=='996'].drop_duplicates(),on="VENDOR_ID",how='left')

In [ ]:
v=df[["VENDOR_ID","ACCOUNT"]][df.c3=='993']
v_1=v.groupby('VENDOR_ID').ACCOUNT.nunique().reset_index()
v_1_993=v_1[v_1.ACCOUNT==1]
v_1_993=v_1_993[["VENDOR_ID"]].merge(df[["VENDOR_ID","ACCOUNT"]][df.c3=='993'].drop_duplicates(),on="VENDOR_ID",how='left')

In [ ]:
v=df[["VENDOR_ID","ACCOUNT"]][df.c3=='997']
v_1=v.groupby('VENDOR_ID').ACCOUNT.nunique().reset_index()
v_1_997=v_1[v_1.ACCOUNT==1]

In [ ]:
v=df[["VENDOR_ID","ACCOUNT"]][df.c3=='994']
v_1=v.groupby('VENDOR_ID').ACCOUNT.nunique().reset_index()
v_1_994=v_1[v_1.ACCOUNT==1]

#### 4.Train Prediction Model